In [1]:
import json
import numpy as np
from engine import SlotGame  # assuming engine.py is in src/
from tqdm import tqdm

def baseline_policy(game: SlotGame):
    # Never buy upgrades, always continue until max rounds or fail
    return None  # no upgrade purchase

def aggressive_policy(game: SlotGame):
    # Buy reel_bias if affordable on first round
    if game.round == 1 and game.credits >= game.config["upgrades"]["reel_bias"]["cost"]:
        return "reel_bias"
    return None

def conservative_policy(game: SlotGame):
    # Buy bar_boost if affordable on round 1, else cash out after first bonus
    if game.round == 1 and game.credits >= game.config["upgrades"]["bar_boost"]["cost"]:
        return "bar_boost"
    if game.round > 1:
        return "cashout"
    return None

def adaptive_ai_policy(game: SlotGame):
    min_cost = min(u["cost"] for u in game.config["upgrades"].values())
    if game.credits < min_cost:
        if game.credits < 50:
            return "cashout"
        return None

    if game.round == 1 and game.credits >= game.config["upgrades"]["reel_bias"]["cost"]:
        return "reel_bias"

    # Use last round's bar progress now!
    if game.last_bar_progress < 0.5 and game.credits >= game.config["upgrades"]["extra_spins"]["cost"]:
        return "extra_spins"

    if game.round >= 2 and game.credits >= game.config["upgrades"]["bar_boost"]["cost"]:
        return "bar_boost"

    if game.credits >= game.config["upgrades"]["bonus_multiplier_upgrade"]["cost"]:
        return "bonus_multiplier_upgrade"

    if game.round >= 3 and game.credits >= 150:
        return "cashout"

    return None


def run_single_sim(config_path, policy_fn):
    game = SlotGame(config_path)
    results = {
        "final_credits": None,
        "rounds_played": 0,
        "bonuses_triggered": 0,
        "upgrades_bought": [],
    }
    while game.round <= game.max_rounds:
        bonus = game.play_round()
        results["rounds_played"] = game.round
        if bonus:
            results["bonuses_triggered"] += 1

        # Query policy for upgrade purchase or cashout
        action = policy_fn(game)
        if action == "cashout":
            break
        elif action is not None and action in game.config["upgrades"]:
            msg = game.buy_upgrade(action)
            results["upgrades_bought"].append(action)

        if not bonus:
            break
        if game.round == game.max_rounds:
            break

        # Difficulty increase: +1 to bar target per round
        game.bar_target += 1.0
        game.round += 1

    results["final_credits"] = game.credits
    return results

def batch_simulate(config_path, policy_fn, num_runs=1000):
    all_results = []
    for _ in tqdm(range(num_runs)):
        res = run_single_sim(config_path, policy_fn)
        all_results.append(res)
    return all_results

def summarize_results(results):
    final_credits = np.array([r["final_credits"] for r in results])
    rounds_played = np.array([r["rounds_played"] for r in results])
    bonuses = np.array([r["bonuses_triggered"] for r in results])

    print(f"Runs: {len(results)}")
    print(f"Average final credits: {final_credits.mean():.2f}")
    print(f"Median final credits: {np.median(final_credits):.2f}")
    print(f"Std dev final credits: {final_credits.std():.2f}")
    print(f"Average rounds played: {rounds_played.mean():.2f}")
    print(f"Average bonuses triggered: {bonuses.mean():.2f}")

if __name__ == "__main__":
    config_path = "D://pythonprojects/game_math/slot-game-project-1/data/example_config.json"

    print("Running baseline policy...")
    baseline_results = batch_simulate(config_path, baseline_policy, num_runs=1000)
    summarize_results(baseline_results)

    print("\nRunning aggressive policy...")
    aggressive_results = batch_simulate(config_path, aggressive_policy, num_runs=1000)
    summarize_results(aggressive_results)

    print("\nRunning conservative policy...")
    conservative_results = batch_simulate(config_path, conservative_policy, num_runs=1000)
    summarize_results(conservative_results)

    print("\nRunning adaptive AI policy...")
    adaptive_results = batch_simulate(config_path, adaptive_ai_policy, num_runs=1000)
    summarize_results(adaptive_results)




Running baseline policy...


 51%|█████     | 510/1000 [00:00<00:00, 2551.18it/s]


Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['D', 'B', 'A'] | Bar filled this spin: 0.0400 | Total bar progress: 0.0400
Spin 2: ['C', 'C', 'B'] | Bar filled this spin: 0.3300 | Total bar progress: 0.3700
Spin 3: ['E', 'E', 'D'] | Bar filled this spin: 0.5500 | Total bar progress: 0.9200
Spin 4: ['A', 'A', 'B'] | Bar filled this spin: 0.1100 | Total bar progress: 1.0000
Spin 5: ['C', 'B', 'A'] | Bar filled this spin: 0.0300 | Total bar progress: 1.0000
Spin 6: ['A', 'C', 'E'] | Bar filled this spin: 0.0500 | Total bar progress: 1.0000
Spin 7: ['A', 'C', 'D'] | Bar filled this spin: 0.0400 | Total bar progress: 1.0000
Bonus triggered! Credits multiplied by 2.0. New credits: 200.0

Round 2 | Bar target: 2.00 | Spins this round: 7 | Credits: 200.0
Spin 1: ['B', 'E', 'E'] | Bar filled this spin: 0.5500 | Total bar progress: 0.5500
Spin 2: ['C', 'D', 'A'] | Bar filled this spin: 0.0400 | Total bar progress: 0.5900
Spin 3: ['A', 'A', 'A'] | Bar filled this spin: 0

 77%|███████▋  | 766/1000 [00:00<00:00, 2206.82it/s]


Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['C', 'D', 'C'] | Bar filled this spin: 0.3300 | Total bar progress: 0.3300
Spin 2: ['A', 'B', 'C'] | Bar filled this spin: 0.0300 | Total bar progress: 0.3600
Spin 3: ['A', 'E', 'B'] | Bar filled this spin: 0.0500 | Total bar progress: 0.4100
Spin 4: ['A', 'A', 'E'] | Bar filled this spin: 0.1100 | Total bar progress: 0.5200
Spin 5: ['B', 'A', 'D'] | Bar filled this spin: 0.0400 | Total bar progress: 0.5600
Spin 6: ['E', 'B', 'C'] | Bar filled this spin: 0.0500 | Total bar progress: 0.6100
Spin 7: ['C', 'B', 'E'] | Bar filled this spin: 0.0500 | Total bar progress: 0.6600
No bonus this round.

Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['C', 'B', 'C'] | Bar filled this spin: 0.3300 | Total bar progress: 0.3300
Spin 2: ['C', 'C', 'C'] | Bar filled this spin: 0.5001 | Total bar progress: 0.8301
Spin 3: ['C', 'D', 'B'] | Bar filled this spin: 0.0400 | Total bar progress: 0.8701
Spin 4: [

...


Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['A', 'C', 'B'] | Bar filled this spin: 0.0300 | Total bar progress: 0.0300
Spin 2: ['D', 'D', 'C'] | Bar filled this spin: 0.4400 | Total bar progress: 0.4700
Spin 3: ['C', 'C', 'D'] | Bar filled this spin: 0.3300 | Total bar progress: 0.8000
Spin 4: ['A', 'A', 'D'] | Bar filled this spin: 0.1100 | Total bar progress: 0.9100
Spin 5: ['E', 'A', 'D'] | Bar filled this spin: 0.0500 | Total bar progress: 0.9600
Spin 6: ['D', 'C', 'A'] | Bar filled this spin: 0.0400 | Total bar progress: 1.0000
Spin 7: ['A', 'C', 'A'] | Bar filled this spin: 0.1100 | Total bar progress: 1.0000
Bonus triggered! Credits multiplied by 2.0. New credits: 200.0

Round 2 | Bar target: 2.00 | Spins this round: 7 | Credits: 170.0
Spin 1: ['A', 'B', 'B'] | Bar filled this spin: 0.2200 | Total bar progress: 0.2200
Spin 2: ['A', 'E', 'E'] | Bar filled this spin: 0.5500 | Total bar progress: 0.7700
Spin 3: ['B', 'E', 'E'] | Bar filled this spin: 0

 87%|████████▋ | 867/1000 [00:00<00:00, 2226.97it/s]


Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['E', 'A', 'D'] | Bar filled this spin: 0.0500 | Total bar progress: 0.0500
Spin 2: ['E', 'E', 'B'] | Bar filled this spin: 0.5500 | Total bar progress: 0.6000
Spin 3: ['D', 'B', 'A'] | Bar filled this spin: 0.0400 | Total bar progress: 0.6400
Spin 4: ['C', 'B', 'D'] | Bar filled this spin: 0.0400 | Total bar progress: 0.6800
Spin 5: ['D', 'C', 'E'] | Bar filled this spin: 0.0500 | Total bar progress: 0.7300
Spin 6: ['C', 'E', 'D'] | Bar filled this spin: 0.0500 | Total bar progress: 0.7800
Spin 7: ['D', 'C', 'A'] | Bar filled this spin: 0.0400 | Total bar progress: 0.8200
No bonus this round.

Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['E', 'A', 'C'] | Bar filled this spin: 0.0500 | Total bar progress: 0.0500
Spin 2: ['E', 'B', 'C'] | Bar filled this spin: 0.0500 | Total bar progress: 0.1000
Spin 3: ['C', 'C', 'B'] | Bar filled this spin: 0.3300 | Total bar progress: 0.4300
Spin 4: [

100%|██████████| 1000/1000 [00:00<00:00, 2103.97it/s]


Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['A', 'D', 'A'] | Bar filled this spin: 0.1100 | Total bar progress: 0.1100
Spin 2: ['C', 'E', 'B'] | Bar filled this spin: 0.0500 | Total bar progress: 0.1600
Spin 3: ['C', 'C', 'E'] | Bar filled this spin: 0.3300 | Total bar progress: 0.4900
Spin 4: ['C', 'A', 'C'] | Bar filled this spin: 0.3300 | Total bar progress: 0.8200
Spin 5: ['E', 'E', 'B'] | Bar filled this spin: 0.5500 | Total bar progress: 1.0000
Spin 6: ['A', 'E', 'B'] | Bar filled this spin: 0.0500 | Total bar progress: 1.0000
Spin 7: ['B', 'A', 'D'] | Bar filled this spin: 0.0400 | Total bar progress: 1.0000
Bonus triggered! Credits multiplied by 2.0. New credits: 200.0

Round 2 | Bar target: 2.00 | Spins this round: 7 | Credits: 170.0
Spin 1: ['E', 'E', 'E'] | Bar filled this spin: 0.8335 | Total bar progress: 0.8335
Spin 2: ['C', 'A', 'C'] | Bar filled this spin: 0.3300 | Total bar progress: 1.1635
Spin 3: ['A', 'B', 'B'] | Bar filled this spin: 0

In [326]:
import numpy as np
from engine import SlotGame

def run_single_sim_verbose(config_path, policy_fn):
    game = SlotGame(config_path)
    print(f"Starting game with credits: {game.credits}")
    print(f"Max rounds allowed: {game.max_rounds}\n")

    while game.round <= game.max_rounds:
        print(f"--- Round {game.round} ---")
        bonus = game.play_round()
        print(f"Credits after round {game.round}: {game.credits:.2f}")
        action = policy_fn(game)
        if action == "cashout":
            print("Player chooses to cash out.")
            break
        elif action is not None and action in game.config["upgrades"]:
            msg = game.buy_upgrade(action)
            print(msg)
        if not bonus:
            print("Bar not filled — game ends.")
            break
        if game.round == game.max_rounds:
            print("Max rounds reached. Game ends.")
            break
        # Increase bar target by 1 per round (or keep your logic)
        game.bar_target += 1.0
        game.round += 1
        print(f"Proceeding to round {game.round} with bar target {game.bar_target:.2f}\n")

    print(f"Game over. Final credits: {game.credits:.2f}")


def adaptive_ai_policy(game: SlotGame):
    print(f"Round: {game.round}, Credits: {game.credits:.2f}, Last bar progress: {game.last_bar_progress:.2f}")
    
    min_cost = min(u["cost"] for u in game.config["upgrades"].values())
    if game.credits < min_cost:
        if game.credits < 50:
            print("Action: cashout (low credits)")
            return "cashout"
        print("Action: continue (not enough credits for upgrades)")
        return None

    if game.round == 1 and game.credits >= game.config["upgrades"]["reel_bias"]["cost"]:
        print("Action: buy reel_bias")
        return "reel_bias"

    if game.last_bar_progress < 0.5 and game.credits >= game.config["upgrades"]["extra_spins"]["cost"]:
        print("Action: buy extra_spins (low bar progress)")
        return "extra_spins"

    if game.round >= 2 and game.credits >= game.config["upgrades"]["bar_boost"]["cost"]:
        print("Action: buy bar_boost")
        return "bar_boost"

    if game.credits >= game.config["upgrades"]["bonus_multiplier_upgrade"]["cost"]:
        print("Action: buy bonus_multiplier_upgrade")
        return "bonus_multiplier_upgrade"

    if game.round >= 3 and game.credits >= 150:
        print("Action: cashout (good credits and round >= 3)")
        return "cashout"

    print("Action: continue")
    return None

if __name__ == "__main__":
    config_path = "D://pythonprojects/game_math/slot-game-project-1/data/example_config.json"


    run_single_sim_verbose(config_path, adaptive_ai_policy)


Starting game with credits: 100
Max rounds allowed: 5

--- Round 1 ---

Round 1 | Bar target: 1.00 | Spins this round: 7 | Credits: 100
Spin 1: ['E', 'C', 'D'] | Bar filled this spin: 0.0500 | Total bar progress: 0.0500
Spin 2: ['B', 'C', 'D'] | Bar filled this spin: 0.0400 | Total bar progress: 0.0900
Spin 3: ['B', 'C', 'C'] | Bar filled this spin: 0.3300 | Total bar progress: 0.4200
Spin 4: ['E', 'E', 'B'] | Bar filled this spin: 0.5500 | Total bar progress: 0.9700
Spin 5: ['D', 'D', 'D'] | Bar filled this spin: 0.6668 | Total bar progress: 1.0000
Spin 6: ['D', 'D', 'C'] | Bar filled this spin: 0.4400 | Total bar progress: 1.0000
Spin 7: ['C', 'C', 'B'] | Bar filled this spin: 0.3300 | Total bar progress: 1.0000
Bonus triggered! Credits multiplied by 2.0. New credits: 200.0
Credits after round 1: 200.00
Round: 1, Credits: 200.00, Last bar progress: 1.00
Action: buy reel_bias
Upgrade reel_bias purchased successfully.
Proceeding to round 2 with bar target 2.00

--- Round 2 ---

Round 2

In [332]:
# stats.py
import itertools
import pandas as pd
from engine import SlotGame 

def export_spin_stats(config_path, filename="D://pythonprojects/game_math/slot-game-project-1/outputs/spin_stats.xlsx"):
    game = SlotGame(config_path)
    symbols = game.symbols
    cols = game.cols
    base_multipliers = game.base_multipliers
    bar_fill_per_match = game.bar_fill_per_match
    symbol_probs = game.symbol_probs

    all_combinations = list(itertools.product(symbols, repeat=cols))
    rows = []

    for outcome in all_combinations:
        adjusted_probs = dict(symbol_probs)  # fresh copy for each outcome
        prob = 1.0
        counts = {s: 0 for s in symbols}

        for sym in outcome:
            total_prob = sum(adjusted_probs.values())
            norm_probs = {s: p / total_prob for s, p in adjusted_probs.items()}
            prob *= norm_probs[sym]
            counts[sym] += 1
            if counts[sym] == 2:
                adjusted_probs[sym] /= 2
            elif counts[sym] >= 3:
                adjusted_probs[sym] /= 4

        # Calculate bar fill increment (no upgrades)
        bar_fill = 0.0
        matched = False

        for sym, count in counts.items():
            if count == 3:
                bar_fill = base_multipliers[sym] * bar_fill_per_match["3_same"]
                matched = True
                break

        if not matched:
            for sym, count in counts.items():
                if count == 2:
                    bar_fill = base_multipliers[sym] * bar_fill_per_match["2_same"]
                    matched = True
                    break

        if not matched:
            singles = [s for s, c in counts.items() if c == 1]
            if singles:
                best_sym = max(singles, key=lambda s: base_multipliers[s])
                bar_fill = base_multipliers[best_sym] * bar_fill_per_match["1_same"]

        rows.append({
            "Outcome": ''.join(outcome),
            "Probability": prob,
            "3_same": any(count == 3 for count in counts.values()),
            "2_same": any(count == 2 for count in counts.values()),
            "1_same": sum(1 for count in counts.values() if count == 1) > 0 and not any(count >= 2 for count in counts.values()),
            "Bar_fill_increment": bar_fill,
        })

    df = pd.DataFrame(rows)
    df.sort_values("Probability", ascending=False, inplace=True)
    df.to_excel(filename, index=False)
    print(f"Exported conditional spin stats to {filename}")


In [334]:
config_path = "D://pythonprojects/game_math/slot-game-project-1/data/example_config.json"
export_spin_stats(config_path)

Exported conditional spin stats to D://pythonprojects/game_math/slot-game-project-1/outputs/spin_stats.xlsx
